# A Guided Tour of QuantumGraph Generation

## Preliminaries

In [1]:
from lsst.pipe.base import Pipeline
from lsst.pipe.base.graphBuilder import _DatasetDict, _PipelineScaffolding
from lsst.daf.butler import Butler, DatasetRef

Set up logging to echo all SQL queries to a file that we can periodically truncate, while sending debug logs from the graph builder algorithm directly to STDERR and hence the notebook outputs.

In [2]:
import logging.handlers
import os

SQL_LOG_FILE = "qggen-tour.log"

def setup_logging():
    pipe_base_logger = logging.getLogger("lsst.pipe.base.graphBuilder")
    pipe_base_logger.setLevel(logging.DEBUG)
    pipe_base_logger.addHandler(logging.StreamHandler())
    sql_logger = logging.getLogger("sqlalchemy.engine")
    sql_logger.setLevel(logging.INFO)
    sql_log_handler = logging.handlers.WatchedFileHandler(SQL_LOG_FILE)
    sql_log_handler.setFormatter(logging.Formatter("%(message)s"))
    sql_logger.addHandler(sql_log_handler)

setup_logging()

def truncate_log():
    os.truncate(SQL_LOG_FILE, 0)


A little utility function to convert data ID query results into `pandas.DataFrame`, just for pretty-printing.

In [3]:
import pandas as pd

def to_table(iterable):
    return pd.DataFrame.from_records(
        [tuple(data_id.full.values()) for data_id in iterable],
        columns=list(iterable.graph.dimensions.names),
    )

A lot of the QG generation algorithm happens within a context manager (`with` statement block), because it creates a temporary table in the database, and that means we need to keep a connection alive for the duration of the algorithm.  Using `with` directly in a notebook would be awkward, so we'll create a `contextlib.ExitStack` to hold the context manager and close it explicitly at the end.

In [4]:
from contextlib import ExitStack
context_managers = ExitStack()

## Inputs to the algorithm

In [5]:
butler = Butler("/repo/dc2", collections="2.2i/defaults/test-med-1")

In [6]:
data_id = butler.registry.expandDataId(instrument="LSSTCam-imSim", skymap="DC2", tract=3828, patch=30)

In [7]:
truncate_log()

In [8]:
pipeline = Pipeline.from_uri(os.path.join(os.environ["DRP_PIPE_DIR"], "pipelines", "LSSTCam-imSim", "DRP-test-med-1.yaml"))

In [9]:
scaffolding = _PipelineScaffolding(pipeline, registry=butler.registry)

Initializing data structures for QuantumGraph generation.


Overriding default configuration file with /project/jbosch/lsstsw/stack/lsst-scipipe-3.0.0/Linux64/dustmaps_cachedata/g41a3ec361e+ce83317b7e/config/.dustmapsrc


In [10]:
print("inputs: ", set(scaffolding.inputs.names))
print("dimensions:", scaffolding.dimensions)

inputs:  {'skyMap', 'cosmodc2_1_1_4_redmapper_v0_8_1_redgals', 'raw', 'truth_summary'}
dimensions: {band, instrument, skymap, detector, physical_filter, tract, visit_system, exposure, patch, visit}


## The Big Data ID Query

First, let's actually run the real version of this step, and watch what happens.

In [11]:
common_data_ids = context_managers.enter_context(
    scaffolding.connectDataIds(
        butler.registry,
        collections=butler.collections,
        userQuery=None,
        externalDataId=data_id,
    )
)
common_data_ids_list = list(set(common_data_ids))
to_table(common_data_ids)

Building query for data IDs.
Submitting data ID query and materializing results.
Constraining graph query using all datasets in pipeline.
Expanding data IDs.
Iterating over query results to associate quanta with datasets.
Finished processing 895 rows from data ID query.


band     instrument skymap  detector physical_filter  tract  visit_system  \
0      g  LSSTCam-imSim    DC2         7       g_sim_1.4   3828             1   
1      g  LSSTCam-imSim    DC2         7       g_sim_1.4   3828             1   
2      g  LSSTCam-imSim    DC2         8       g_sim_1.4   3828             1   
3      g  LSSTCam-imSim    DC2         8       g_sim_1.4   3828             1   
4      g  LSSTCam-imSim    DC2        11       g_sim_1.4   3828             1   
..   ...            ...    ...       ...             ...    ...           ...   
891    z  LSSTCam-imSim    DC2       185       z_sim_1.4   3828             1   
892    z  LSSTCam-imSim    DC2       185       z_sim_1.4   3828             1   
893    z  LSSTCam-imSim    DC2       187       z_sim_1.4   3828             1   
894    z  LSSTCam-imSim    DC2       188       z_sim_1.4   3828             1   
895    z  LSSTCam-imSim    DC2       188       z_sim_1.4   3828             1   

     exposure  patch   visit  
0      183818     30  183818  
1      183818     30  183818  
2      183818     30  183818  
3      183818     30  183818  
4      221616     30  221616  
..        ...    ...     ...  
891      7998     30    7998  
892      7998     30    7998  
893      7998     30    7998  
894      7998     30    7998  
895      7998     30    7998  

[896 rows x 10 columns]

The query to generate this table can be quite complicated:

In [ ]:
INSERT INTO tmp_709aa56202ca4c09b2539b7a7512dd2f (
        band,
        instrument,
        skymap,
        detector,
        physical_filter,
        tract,
        visit_system,
        exposure,
        patch,
        visit,
        visit_detector_region_region
    )
SELECT physical_filter.band AS band,
    physical_filter.instrument AS instrument,
    patch.skymap AS skymap,
    visit_detector_region.detector AS detector,
    physical_filter.name AS physical_filter,
    patch.tract AS tract,
    visit.visit_system AS visit_system,
    exposure.id AS exposure,
    patch.id AS patch,
    visit.id AS visit,
    visit_detector_region.region AS visit_detector_region_region
FROM (
        SELECT dataset_tags_00000001.skymap AS skymap
        FROM dataset_tags_00000001
        WHERE dataset_tags_00000001.dataset_type_id = %(dataset_type_id_1) s
            AND dataset_tags_00000001.collection_name = %(collection_name_1) s
    ) AS "skyMap"
    JOIN (
        SELECT dataset_tags_00000015.skymap AS skymap,
            dataset_tags_00000015.tract AS tract
        FROM dataset_tags_00000015
        WHERE dataset_tags_00000015.dataset_type_id = %(dataset_type_id_2) s
            AND dataset_tags_00000015.collection_name = %(collection_name_2) s
    ) AS truth_summary ON "skyMap".skymap = truth_summary.skymap
    JOIN (
        SELECT dataset_tags_00000003.instrument AS instrument,
            dataset_tags_00000003.detector AS detector,
            dataset_tags_00000003.exposure AS exposure
        FROM dataset_tags_00000003
        WHERE dataset_tags_00000003.dataset_type_id = %(dataset_type_id_3) s
            AND dataset_tags_00000003.collection_name = %(collection_name_3) s
    ) AS raw ON %(param_1) s
    JOIN (
        SELECT dataset_tags_00000000.dataset_id AS id
        FROM dataset_tags_00000000
        WHERE dataset_tags_00000000.dataset_type_id = %(dataset_type_id_4) s
            AND dataset_tags_00000000.collection_name = %(collection_name_4) s
    ) AS cosmodc2_1_1_4_redmapper_v0_8_1_redgals ON %(param_2) s
    JOIN (
        SELECT visit_detector_region_skypix_overlap.skypix_index AS htm7,
            visit_detector_region_skypix_overlap.instrument AS instrument,
            visit_detector_region_skypix_overlap.detector AS detector,
            visit_detector_region_skypix_overlap.visit AS visit
        FROM visit_detector_region_skypix_overlap
        WHERE visit_detector_region_skypix_overlap.skypix_system = %(skypix_system_1) s
            AND visit_detector_region_skypix_overlap.skypix_level = %(skypix_level_1) s
    ) AS visit_detector_region_htm7_overlap ON raw.instrument = visit_detector_region_htm7_overlap.instrument
    AND raw.detector = visit_detector_region_htm7_overlap.detector
    JOIN visit_detector_region ON raw.instrument = visit_detector_region.instrument
    AND visit_detector_region_htm7_overlap.instrument = visit_detector_region.instrument
    AND raw.detector = visit_detector_region.detector
    AND visit_detector_region_htm7_overlap.detector = visit_detector_region.detector
    AND visit_detector_region_htm7_overlap.visit = visit_detector_region.visit
    JOIN visit_definition ON raw.instrument = visit_definition.instrument
    AND visit_detector_region_htm7_overlap.instrument = visit_definition.instrument
    AND visit_detector_region.instrument = visit_definition.instrument
    AND raw.exposure = visit_definition.exposure
    AND visit_detector_region_htm7_overlap.visit = visit_definition.visit
    AND visit_detector_region.visit = visit_definition.visit
    JOIN visit ON raw.instrument = visit.instrument
    AND visit_detector_region_htm7_overlap.instrument = visit.instrument
    AND visit_detector_region.instrument = visit.instrument
    AND visit_definition.instrument = visit.instrument
    AND visit_detector_region_htm7_overlap.visit = visit.id
    AND visit_detector_region.visit = visit.id
    AND visit_definition.visit = visit.id
    AND visit_definition.visit_system = visit.visit_system
    JOIN exposure ON raw.instrument = exposure.instrument
    AND visit_detector_region_htm7_overlap.instrument = exposure.instrument
    AND visit_detector_region.instrument = exposure.instrument
    AND visit_definition.instrument = exposure.instrument
    AND visit.instrument = exposure.instrument
    AND raw.exposure = exposure.id
    AND visit_definition.exposure = exposure.id
    AND visit.physical_filter = exposure.physical_filter
    JOIN physical_filter ON raw.instrument = physical_filter.instrument
    AND visit_detector_region_htm7_overlap.instrument = physical_filter.instrument
    AND visit_detector_region.instrument = physical_filter.instrument
    AND visit_definition.instrument = physical_filter.instrument
    AND visit.instrument = physical_filter.instrument
    AND exposure.instrument = physical_filter.instrument
    AND visit.physical_filter = physical_filter.name
    AND exposure.physical_filter = physical_filter.name
    JOIN patch ON "skyMap".skymap = patch.skymap
    AND truth_summary.skymap = patch.skymap
    AND truth_summary.tract = patch.tract
WHERE "skyMap".skymap = %(skymap_1) s
    AND truth_summary.skymap = %(skymap_2) s
    AND patch.skymap = %(skymap_3) s
    AND truth_summary.tract = %(tract_1) s
    AND patch.tract = %(tract_2) s
    AND raw.instrument = %(instrument_1) s
    AND visit_detector_region_htm7_overlap.instrument = %(instrument_2) s
    AND visit_detector_region.instrument = %(instrument_3) s
    AND visit_definition.instrument = %(instrument_4) s
    AND visit.instrument = %(instrument_5) s
    AND exposure.instrument = %(instrument_6) s
    AND physical_filter.instrument = %(instrument_7) s
    AND visit_detector_region_htm7_overlap.htm7 IN (%(htm7_1_1) s, %(htm7_1_2) s)
    AND patch.id = %(id_1) s

We're very much relying on the databases's query planner coming up with an efficient way to execute it.  It doesn't always succeed, and that's one big cause of slow QG generation.

In [12]:
truncate_log()

This query returning no rows is the classic way to get an empty `QuantumGraph`, and I hope this makes it clear why it took us a while to improve diagnostics associated with that particular error: we gave the database a big query, and it gave us nothing back.

If you haven't experienced an empty QG in the past few months, congratulations, and also it's a lot beter about providing hints now, for two reasons:

- When building the SQL query itself, we make use of "collection summaries" that remember which dataset types and instrument data ID values are present in each collection.  That lets us simplify the query itself by avoiding searches that are doomed to fail, and it also lets us detect when there are no collections at all in which a particular dataset type can be found.
- If we get no results from actually running a non-doomed query, we now perform some follow-up similar queries to check for common problems, in the hopes that one of those will have no results on its own and thus pinpoint the problem.

Most of the steps in the log messages above happen on the database server.  The exception is this one:

> Iterating over query results to associate quanta with datasets.

This is worth a closer look, so I've extracted the body of the loop into a function we can call one at a time, after simplying it and making it print instead of actually doing anything.

In [16]:
# Make a data structure like scaffolding.{inputs, outputs, intermediates} so we
# can watch what happens to it in our (simplified) single-row run-through of
# connectDataIds.  We'll just watch two dataset types, instead of all of them.
scaffolding_datasets = _DatasetDict.fromDatasetTypes(
    [scaffolding.inputs.keys()["raw"], scaffolding.intermediates.keys()["deepCoadd_directWarp"]],
    universe=butler.registry.dimensions,
)

def connect_one_row(common_data_id):
    """A simplified, verbose, incomplete version of the loop body in
    connectDataIds.
    """
    print("common_data_id:", common_data_id.full)
    print("")
    # Create DatasetRefs for all DatasetTypes from this result row,
    # noting that we might have created some already.
    # We remember both those that already existed and those that we
    # create now.
    refs_for_row = {}
    for dataset_type, refs in scaffolding_datasets.items():
        dataset_data_id = common_data_id.subset(dataset_type.dimensions)
        ref = refs.get(dataset_data_id)
        if ref is None:
            ref = DatasetRef(dataset_type, dataset_data_id)
            refs[dataset_data_id] = ref
        refs_for_row[dataset_type.name] = ref
    print("refs_for_row:", refs_for_row)
    print("")
    # Create _QuantumScaffolding objects for all tasks from this
    # result row, noting that we might have created some already.
    for task in scaffolding.tasks:
        quantum_data_id = common_data_id.subset(task.dimensions)
        # Whether this is a new quantum or an existing one, we can
        # now associate the DatasetRefs for this row with it.  The
        # fact that a Quantum data ID and a dataset data ID both
        # came from the same result row is what tells us they
        # should be associated.
        # Many of these associates will be duplicates (because
        # another query row that differed from this one only in
        # irrelevant dimensions already added them), and we use
        # sets to skip.
        for dataset_type in task.inputs:
            if dataset_type.name in refs_for_row:  # check only necessary because we're only doing inputs
                ref = refs_for_row[dataset_type.name]
                print(
                    f"Connecting quantum {task.taskDef.label}@{quantum_data_id} "
                    f"to input {dataset_type.name}@{ref.dataId}."
                )
        # for dataset_type in task.outputs:
        #     ref = refs_for_row[dataset_type.name]
        #     quantum.outputs[dataset_type.name][ref.dataId] = ref
    print("")

In [17]:
common_data_ids_list = list(set(common_data_ids))
connect_one_row(common_data_ids_list[0])

common_data_id: {band: 'i', instrument: 'LSSTCam-imSim', skymap: 'DC2', detector: 133, physical_filter: 'i_sim_1.4', tract: 3828, visit_system: 1, exposure: 457681, patch: 30, visit: 457681}

refs_for_row: {'raw': DatasetRef(DatasetType('raw', {band, instrument, detector, physical_filter, exposure}, Exposure), {instrument: 'LSSTCam-imSim', detector: 133, exposure: 457681, ...}), 'deepCoadd_directWarp': DatasetRef(DatasetType('deepCoadd_directWarp', {band, instrument, skymap, physical_filter, tract, visit_system, patch, visit}, ExposureF), {instrument: 'LSSTCam-imSim', skymap: 'DC2', tract: 3828, patch: 30, visit: 457681, ...})}

Connecting quantum isr@{instrument: 'LSSTCam-imSim', detector: 133, exposure: 457681, ...} to input raw@{instrument: 'LSSTCam-imSim', detector: 133, exposure: 457681, ...}.
Connecting quantum assembleCoadd@{band: 'i', skymap: 'DC2', tract: 3828, patch: 30} to input deepCoadd_directWarp@{instrument: 'LSSTCam-imSim', skymap: 'DC2', tract: 3828, patch: 30, visit: 

In [18]:
connect_one_row(common_data_ids_list[1])

common_data_id: {band: 'g', instrument: 'LSSTCam-imSim', skymap: 'DC2', detector: 167, physical_filter: 'g_sim_1.4', tract: 3828, visit_system: 1, exposure: 254407, patch: 30, visit: 254407}

refs_for_row: {'raw': DatasetRef(DatasetType('raw', {band, instrument, detector, physical_filter, exposure}, Exposure), {instrument: 'LSSTCam-imSim', detector: 167, exposure: 254407, ...}), 'deepCoadd_directWarp': DatasetRef(DatasetType('deepCoadd_directWarp', {band, instrument, skymap, physical_filter, tract, visit_system, patch, visit}, ExposureF), {instrument: 'LSSTCam-imSim', skymap: 'DC2', tract: 3828, patch: 30, visit: 254407, ...})}

Connecting quantum isr@{instrument: 'LSSTCam-imSim', detector: 167, exposure: 254407, ...} to input raw@{instrument: 'LSSTCam-imSim', detector: 167, exposure: 254407, ...}.
Connecting quantum assembleCoadd@{band: 'g', skymap: 'DC2', tract: 3828, patch: 30} to input deepCoadd_directWarp@{instrument: 'LSSTCam-imSim', skymap: 'DC2', tract: 3828, patch: 30, visit: 

I want to take a moment to highlight this comment from the code block earlier, which is taken from the real code in `pipe_base`:

> The fact that a Quantum data ID and a dataset data ID both came from the same result row is what tells us they should be associated.

This is frankly the fundamental guts of the entire algorithm, and while some past version of myself can probably take some of the credit for the idea (Andy Salnikov certains gets credit for transforming vague hand-waving and whiteboard diagrams to something concrete, and everyone in middleware contributed some), it nevertheless feels somewhat magical.

This statement translates the problem from the directed acyclic graph space (where I think it's relatively easy to understand) to the relational algebra that underpins a SQL database.  It's what connects `PipelineTask` to `Butler`.


But this loop can actually be pretty expensive, for a number of reasons:
- the classes it uses have too many `isinstance` checks (RFC-834);
- there's potentially a lot of duplication, because any particular task or dataset only cares about some of the dimensions.

There's probably a lot of room for improvement - this only recently appeared on my radar as a bottleneck - for example by working on numpy-backed tables rather than `DataCoordinate` instances.  But fundamentally we want to change the algorithm itself to reduce the need for deduplication, and we have a new one in mind that solves other problems as well.

In [19]:
truncate_log()

## Resolving datasets

In [20]:
scaffolding.resolveDatasetRefs(
    butler.registry,
    butler.collections,
    None,
    common_data_ids
)

Resolving 544 datasets for input dataset raw.
Resolving 1 datasets for input dataset skyMap.
Resolving 1 datasets for input dataset truth_summary.
Resolving 1 datasets for input dataset cosmodc2_1_1_4_redmapper_v0_8_1_redgals.
Applying resolutions and finding prerequisites for 544 quanta of task with label 'isr'.
Applying resolutions and finding prerequisites for 544 quanta of task with label 'characterizeImage'.
Applying resolutions and finding prerequisites for 544 quanta of task with label 'calibrate'.
Applying resolutions and finding prerequisites for 132 quanta of task with label 'TE3'.
Applying resolutions and finding prerequisites for 132 quanta of task with label 'TE4'.
Applying resolutions and finding prerequisites for 132 quanta of task with label 'consolidateVisitSummary'.
Applying resolutions and finding prerequisites for 1 quanta of task with label 'makeCcdVisitTable'.
Applying resolutions and finding prerequisites for 1 quanta of task with label 'makeVisitTable'.
Applying

This step involves two very different kinds of queries.  For regular input datasets (and output datasets, when writing to an existing `RUN` collection), we do a bulk search for all datasets of a particular type by joining to the temporary table of data IDs.

For example:

In [ ]:
SELECT
    anon_1.band AS band,
    raw.instrument AS instrument,
    raw.detector AS detector,
    anon_1.physical_filter AS physical_filter,
    raw.exposure AS exposure,
    raw.id AS dataset_id,
    raw.run_name AS run_name
FROM (
        SELECT DISTINCT
            tmp_94e04ac3b16b487d8ceed49abfe26c55.band AS band,
            tmp_94e04ac3b16b487d8ceed49abfe26c55.instrument AS instrument,
            tmp_94e04ac3b16b487d8ceed49abfe26c55.detector AS detector,
            tmp_94e04ac3b16b487d8ceed49abfe26c55.physical_filter AS physical_filter,
            tmp_94e04ac3b16b487d8ceed49abfe26c55.exposure AS exposure
        FROM tmp_94e04ac3b16b487d8ceed49abfe26c55
    ) AS anon_1
    JOIN (
        SELECT
            dataset_tags_00000003.instrument AS instrument,
            dataset_tags_00000003.detector AS detector,
            dataset_tags_00000003.exposure AS exposure,
            dataset_tags_00000003.dataset_id AS id,
            dataset.run_name AS run_name,
            dataset.ingest_date AS ingest_date
        FROM dataset_tags_00000003
            JOIN dataset ON dataset_tags_00000003.dataset_id = dataset.id
        WHERE dataset_tags_00000003.dataset_type_id = %(dataset_type_id_1) s
            AND dataset_tags_00000003.collection_name = %(collection_name_1) s
            AND dataset.dataset_type_id = %(dataset_type_id_2) s
    ) AS raw ON anon_1.instrument = raw.instrument
    AND anon_1.detector = raw.detector
    AND anon_1.exposure = raw.exposure

This particular query is pretty simple, because we're only searching one collection that has any `raw` datasets at all.  When there are more - and the query needs to pick out the one from the first collection in an ordered list - it gets a lot more complicated.  Either because that more complicated scenario is rare in practice or because it's not hard for the query planner to deal with anyway, these queries rarely seem to be bottlenecks.

The queries for prerequisites look different, and in fact they don't all look alike - in some sense that's because prerequisites are our escape valve for things the rest of `QuantumGraph` generation can't handle.

Here's a query for reference catalog lookup:

In [ ]:
SELECT
    cal_ref_cat_2_2.htm7 AS htm7,
    cal_ref_cat_2_2.id AS dataset_id,
    cal_ref_cat_2_2.run_name AS run_name
FROM (
        SELECT
            dataset_tags_00000002.htm7 AS htm7,
            dataset_tags_00000002.dataset_id AS id,
            %(param_1)s AS run_name,
            dataset.ingest_date AS ingest_date
        FROM dataset_tags_00000002
            JOIN dataset ON dataset_tags_00000002.dataset_id = dataset.id
        WHERE dataset_tags_00000002.dataset_type_id = %(dataset_type_id_1)s
            AND dataset_tags_00000002.collection_name = %(collection_name_1)s
            AND dataset.dataset_type_id = %(dataset_type_id_2)s
    ) AS cal_ref_cat_2_2
WHERE cal_ref_cat_2_2.htm7 IN (%(htm7_1_1)s, %(htm7_1_2)s)

And here's one for some kind of calibration lookup (can't tell if it's a `flat` or a `fringe` without the bind parameters):

In [ ]:
SELECT dataset_calibs_00000009.dataset_id AS id,
    dataset.run_name AS run_name
FROM dataset_calibs_00000009
    JOIN dataset ON dataset_calibs_00000009.dataset_id = dataset.id
WHERE (
        dataset_calibs_00000009.timespan && %(param_1)s
    )
    AND dataset_calibs_00000009.instrument = %(instrument_1)s
    AND dataset_calibs_00000009.detector = %(detector_1)s
    AND dataset_calibs_00000009.physical_filter = %(physical_filter_1)s
    AND dataset_calibs_00000009.dataset_type_id = %(dataset_type_id_1)s
    AND dataset_calibs_00000009.collection_name = %(collection_name_1)s
    AND dataset.dataset_type_id = %(dataset_type_id_2)s

Individually these prerequisite lookups are super fast, but we run one such query for every (dataset type)x(quantum) combination, while the queries for regular inputs and outputs are just one per dataset type.  That's a massive difference, and the overheads assocated with those many tiny queries is usually the bottleneck in generating `QuantumGraphs` for pipelines that involve ISR (since it has a lot prerequisites).

## Adjusting and finalizing quanta

In [21]:
graph = scaffolding.makeQuantumGraph()

Most of this stuff is just non-algorithmic bookkeeping - transforming the mutable "scaffolding" data structures we used to build the graph into the immutable leaner ones that comprise a `QuantumGraph` object.

The only important algorithmic piece here is that we call `PipelineTaskConnections.adjustQuantum` on each quantum, giving each `PipelineTask` an opportunity to:

- prune out any input datasets it won't actually use;
- prune out any output datasets it won't actually produce;
- prune the quantum entirely if it doesn't have any work to do.

At present, we don't fully propagate these changes between quanta (e.g. if a quantum doesn't produce an output, some other quantum might not get an input), and we get away with that because we also run `adjustQuantum` later, right before each quantum is executed, and can skip at that point if there's no work to do.  It'd be better to prune earlier, and someday we will.

In [22]:
context_managers.close()

## Bottleneck recap and mitigation strategies

We saw three places that can each be the bottleneck for different graph generation problems, and each comes with its own set of strategies for mitigating the problem.  If you've got a graph generation problem that you either suspect or know to be slow, turning on `DEBUG` logs for the `lsst.pipe.base.graphBuilder` logger should make it clear which of those problems you're suffering from.

### Bad execution plan for the Big Data ID Query

This is the only bottleneck that can get really catastrophically bad, in that a bad query plan can make execution scale with the size of the data repository rather than the size of the graph you're trying to build.  The general mitigation strategy here is to try to simplify that query so the query planner can reason about it better.  There are a few ways to do that:

- If you have a lot of overall regular-input dataset types, use the `--dataset-query-constraint` option to control which dataset existence checks are included in Big Data ID Query, because it's those dataset subqueries that really add complexity to the query.  It's very important for the Big Data ID Query to include any dataset types whose existence in a collection significantly constrains the graph, and unhelpful to include any others (but the default is to include them all, since the system can't easily tell which are which).
- Provide more information in the `WHERE`/`-d` expression, and in particular constrain anything spatial (`tract`, `visit`) there, if at all possible.
- Split the pipeline up by task and make multiple QGs, with an eye towards keeping some dimensions out of some subsets entirely.

### Slow connection-building between datasets and quanta

This bottleneck isn't quite linear in the size of the graph (which is the best scaling we can hope for), because the time it takes to connect up quanta and dataset for some task A depends on the number of data IDs for some other task B that may not have any dimensions in common.  My guess is that this penalty is typically a factor of 2-8 - it's the number of detectors a patch typically overlaps or vice versa, and hence the typical number of duplicate rows for typical subsets of dimensions.

The only mitigation here is to split up the pipeline to reduce the number of dimensions in any particular graph generation problem, or to at least limit the number of tasks in any graph generation problems that have a lot of dimensions.  This isn't the reason for DRP's `stepN` subsets, but using those does help with this problem (though they may also exacerbate the previous one for intermediate steps, since those can have a lot of regular-input dataset types).

### Death by a thousand tiny prerequisite lookups

This bottleneck is linear in the size of the graph (or at least linear in the number of total prerequisite datasets in the graph), which is what we want, but that doesn't make it any less annoying when it's getting in your way.

This problem is one that's best to just wait out, unless the duration is hitting some threshold that causes new problems (e.g. timeouts).  If that's the case, splitting up the work further by data ID will help more than splitting it up by task, but you probably won't see overall gains in either case.

## Past and future

Caveat: Jim's memory is not that great.

### Round 1

The very first version of the `QuantumGraph` generation algorithm was essentially *just* the Big Data ID Query, followed by prerequisite lookups (once we added the prerequisite input concept, a bit later).  Instead of resolving regular input and intermediate datasets in follow-up queries, we included that in the initial query, adding columns for the IDs of all those datasets as well.  On the surface, this made a lot of sense: we needed to include at least some of those datasets in the query to constrain it, so why not get the IDs of those datasets back at the same time?

There were two problems:
- There are usually a lot more intermediates than inputs, so this really does make the Big Data ID Query a lot bigger.
- A subquery for "does this dataset exist in at least one of the input collections" is relatively easy to write in SQL, but a subquery for "find the first collection in this list in which this dataset exists" is a lot harder - so the Big Data ID Query got a lot more complex, too.

The result was that the bottleneck was essentially always a bad query plan, because we were giving the database a really hard problem.  IIRC, it usually took _days_ to make a `QuantumGraph` for a single RC2 tract.

### Round 2

The next version directly addressed those problems by removing the intermediate datasets from the Big Data ID Query, and making the input dataset searches there the simpler version that just constrains the data IDs rather than trying to seach collections in order.  That means we had to perform follow-up queries to resolve those, as we do today.

In this version, however, we didn't put the results of the Big Data ID Query into a temporary table - we just fetched them all to Python, and did the follow-up dataset queries _one data ID at a time_.

It was death by a thousand prerequisite lookups, multiplied by a factor of 10 or so.  But the time to make a `QuantumGraph` for my favorite RC2 test tract went down to about 5 hours.

### Round 3

This is essentially the version of `QuantumGraph` generation we have today: the Big Data ID query results go into a temporary table, allowing bulk searches for all but prerequisite inputs.  The single-tract RC2 benchmark came down to about an hour.

Since then, the performance improvements have been minor, and more driven by other things, like the collection summaries that improve diagnostics as well as simplify some dataset subqueries.

The most recent addition is the `--dataset-query-constraint` option added by Nate Lust a few months ago, which can help a _lot_ for some problems, but doesn't matter at all for others.

### The Infamous DM-21904

Back in the Round 1 era (November 2019!), Nate Lust and I sketched out a pretty rigorous plan for a new `QuantumGraph` generation algorithm on a whiteboard, and wrote it down on [DM-21904](https://jira.lsstcorp.org/browse/DM-21904).  By having smaller, per-`PipelineTask` data ID queries instead of one big one up front, and walking the tasks in the pipeline in a certain order, we could:

- remove all of the special-casing and constraints involving prerequisite inputs, fully unifying them with regular inputs;
- give individual tasks control over how different dimensions were spatially joined, removing a major blocker for running more steps together;
- provide much better diagnostics for empty QGs;
- _hopefully_ address lot of Big Data ID Query slowdown problems, by replacing that big query with a few smaller, simpler ones.

While Nate got to work implementing this, I worked on smaller-scale, more direct optimizations to the existing algorithm, leading to the Round 2 improvements.  But that revealed something troubling: per-query overheads were significant enough that we really had to move towards bulk searches instead of tiny per-data-ID queries, and that glorious new algorithm we'd sketched out was entirely dependent on being able to do a lot _more_ tiny queries.  Nate's branch was almost certainly a dead end.

The algorithmic idea itself isn't dead - Nate and I came up with a variant (if not quite at the same level of rigor) that allows each Task to pass its state to the next one via temporary tables, instead of Python, keeping it all on the server and enabling everything to be done with bulk queries.  But it needed new Butler query system support, and that's something I've been promising Nate for 2.5 years now.  I am actually working on it pretty steadily now, finally, so I'm hoping we won't get to three years.

When we finally get this done, I do think it will solve all of our _current_ `QuantumGraph` generation slowdowns: there will be no single big query, the dataset-quantum connections won't have as much duplication (an advantage of the algorithm we hadn't anticipated back when we came up with it), and the query system improvements themselves will let us finally replace the prerequisite lookups with real `queryDatasets` support for calibrations.